<h1 style="text-align: center;">Lecture 01 Computer Arithmetic</h1>

We will use Python and numpy as tools to demonostrate how Floating-point arithmetic via IEEE 754.

In [101]:
import sys
import math
import warnings
import numpy as np
from IPython.display import display, HTML

### 1. How to calculate $\sqrt{2}$?

> Let $x = \sqrt{2}$. We assume our first guess is x0 = 2, and we observed that the average of x0 and 2/x0 is a better estimate of x. This idea leads to the following updates:


$$
x_{t+1} = \frac{1}{2}\left( x_t + \frac{1}{x_t}\right), \text{ for } t = 0, 1, 2, \ldots,
$$

Let us verify this!

In [56]:
# We will use decimal to show above example.
from decimal import *
getcontext().prec = 64 # To set precision
x = Decimal(1.0) / Decimal(3.0)
print(x)

0.3333333333333333333333333333333333333333333333333333333333333333


In [58]:
x = Decimal(2).sqrt()
print(' x: ', x)
xt = Decimal(2.0)
for i in range(6):
    xt = Decimal(0.5) * (xt + Decimal(2.) / xt)
    prec_digits = -Decimal.log10(xt - x)
    print('xt: ', xt, 'significant digits of precision: ', int(math.ceil(float(prec_digits))))

 x:  1.414213562373095048801688724209698078569671875376948073176679738
xt:  1.5 significant digits of precision:  2
xt:  1.416666666666666666666666666666666666666666666666666666666666666 significant digits of precision:  3
xt:  1.414215686274509803921568627450980392156862745098039215686274510 significant digits of precision:  6
xt:  1.414213562374689910626295578890134910116559622115744044584905019 significant digits of precision:  12
xt:  1.414213562373095048801689623502530243614981925776197428498289498 significant digits of precision:  25
xt:  1.414213562373095048801688724209698078569671875377234001561013133 significant digits of precision:  49


**Key observation:** Above results indicate that the solution obtains doubled precision per-iteration.

### 2. Python has built-in functions and types for numerical values.

There are three distinct numeric types: integers, floating-point numbers, and complex numbers. In addition, Booleans are a subtype of integers. Integers have unlimited precision. Floating-point numbers are usually implemented using double in C; information about the precision and internal representation of floating-point numbers for the machine on which your program is running is available in sys.float_info. Complex numbers have a real and imaginary part, which are each a floating-point number. To extract these parts from a complex number z, use z.real and z.imag. (See more in [Link](https://docs.python.org/3/library/stdtypes.html#numeric-types-int-float-complex))

Convert an integer number to a binary string prefixed with “0b”. The result is a valid Python expression. If x is not a Python int object, it has to define an __index__() method that returns an integer. ([See the link](https://docs.python.org/3.12/library/functions.html#bin))

In [14]:
print(bin(3))
print(bin(0))
print(bin(-0))
print(bin(-100))

0b11
0b0
0b0
-0b1100100


In [10]:
bin(-100)

'-0b1100100'

In [21]:
# Printing the integer conversions
print(int(123.45))  # 123 (truncates the decimal part)
print(int('123'))  # 123 (from string)
print(int('   -12_345\n'))  # -12345 (whitespace and underscores ignored)
print(int('FACE', 16))  # 64206 (interpreted as a hexadecimal)
print(int('0xface', 0))  # 64206 (auto-detects hex due to '0x')
print(int('01110011', base=2))  # 115 (interpreted as binary)

123
123
-12345
64206
64206
115


In [75]:
print(hex(255))
print(hex(-42))

0xff
-0x2a


In [67]:
x = 1
print(type(x)) # <class 'int'>
print(sys.getsizeof(x)) # 28
y = 1.0 # x will be 
print(type(y))
print(sys.getsizeof(y)) # 28
z = 1. + 1j
print(type(z))
print(sys.getsizeof(z))

<class 'int'>
28
<class 'float'>
24
<class 'complex'>
32


In [70]:
print(sys.getsizeof(0))
print(sys.getsizeof(1))
print(sys.getsizeof(2 ** 30 - 1))
print(sys.getsizeof(2 ** 30)) # it will automatically expanding
print(sys.getsizeof(2 ** 60 - 1))
print(sys.getsizeof(2 ** 60)) # it will automatically expanding
y = 2 ** 6000 # it will print any integer until you do not have enough memory.
print(y)

24
28
28
32
32
36
1513470582304237072513410067329391955423482356622077508836389416646889306993564534635830817676552455824162236150182627025523267446014684388515185452610872385131925014977944482910893194864870039450549067298170721939711827195277899152348801107671644590882157659897905715342306574668169658354699728703352747795407934837779271083755217530954282733292552820320384388452736605849854097009866199175847289532126439677946323677218741195176031143605520246681993939075046911841617410627221987267713724332646446061053160572807286503464245558500643221584631072641658731573097806459864337910226647829569494284055229751599736619753728848188090692318773574702174698843299086831373062575703757942149263399264787530048897154373819381136097105118607145954825590031647682047062652157439770794084025717418220995063370720546665168546633747096935011148065108431975289654040627344874607009807315363771104716985869481861040739858883444667635709902593581610755376089941291884120821811227210157156298148402819

Memory size of an int data type:

> In Python, integers are objects, not just primitive data types like in languages such as C or Java. A Python int object contains additional information besides just the raw numeric value. The typical overhead for a Python object is 24 bytes on a 64-bit system, and for an integer (int), an additional 4 bytes are needed to store the integer’s value (or more for larger integers). This leads to a total size of 28 bytes (24 + 4 = 28).

Memory Size of a float data type:

> Object overhead: Same as for any Python object, 24 bytes.
> Floating-point value: The value of the float (which is 8 bytes in most systems, as it’s typically a C double). However, the total size for a floating-point number doesn’t add extra bytes beyond the 24 bytes, because the float value is stored directly in the object structure. Thus, for y = 1.0:
> Total size: 24 bytes (which includes the 8 bytes for the float value).

In [71]:
y = 10. ** 308.
print(y)
y = 10. ** 309.
print(y)

1e+308


OverflowError: (34, 'Result too large')

In [74]:
# Printing the complex numbers
print(complex('+1.23'))  # (1.23+0j)
print(complex('-4.5j'))  # (-0-4.5j)
print(complex('-1.23+4.5j'))  # (-1.23+4.5j)
print(complex('\t( -1.23+4.5J )\n'))  # (-1.23+4.5j)
print(complex('-Infinity+NaNj'))  # (-inf+nanj)
print(complex(1.23))  # (1.23+0j)
print(complex(imag=-4.5))  # (-0-4.5j)
print(complex(-1.23, 4.5))  # (-1.23+4.5j)
x = complex(-1.23, 4.5)
print(sys.getsizeof(x)) # we have two floats to present x

(1.23+0j)
-4.5j
(-1.23+4.5j)
(-1.23+4.5j)
(-inf+nanj)
(1.23+0j)
-4.5j
(-1.23+4.5j)
32


In [76]:
# Check more details

import sys
print(sys.float_info)
print(sys.float_info.max)
for item in sys.float_info:
    print(item)

sys.float_info(max=1.7976931348623157e+308, max_exp=1024, max_10_exp=308, min=2.2250738585072014e-308, min_exp=-1021, min_10_exp=-307, dig=15, mant_dig=53, epsilon=2.220446049250313e-16, radix=2, rounds=1)
1.7976931348623157e+308
1.7976931348623157e+308
1024
308
2.2250738585072014e-308
-1021
-307
15
53
2.220446049250313e-16
2
1


Machine epsilon 

> Machine epslion is the smallest value that can distinguish 1.0 from the next representable floating-point number, and it is critical for understanding the precision limits of floating-point arithmetic in Python.

In [66]:
# machine epsilon
print(sys.float_info.epsilon)

2.220446049250313e-16


In [68]:
print(2 ** -52)
print(2 ** -52 == sys.float_info.epsilon)

2.220446049250313e-16
True


In [71]:
# Printing the floating-point numbers
print(float('+1.23'))  # 1.23
print(float('   -12345\n'))  # -12345.0
print(float('1e-003'))  # 0.001
print(float('+1E6'))  # 1000000.0
print(float('-Infinity'))  # -inf

1.23
-12345.0
0.001
1000000.0
-inf


### 2. IEEE 754 via Numpy

> There are 5 basic numerical types representing booleans (bool), integers (int), unsigned integers (uint) floating point (float) and complex. A basic numerical type name combined with a numeric bitsize defines a concrete type. The bitsize is the number of bits that are needed to represent a single value in memory. For example, np.float64 is a 64 bit floating point data type. Some types, such as np.int_ and np.intp, have differing bitsizes, dependent on the platforms (e.g. 32-bit vs. 64-bit CPU architectures). This should be taken into account when interfacing with low-level code (such as C or Fortran) where the raw memory is addressed.

| Canonical Python API name                    | Python API "C-like" name        | Actual C type                                  | Description                                                                                  |
|---------------------------------------------------------|--------------------------------------------|------------------------------------------------|----------------------------------------------------------------------------------------------|
| `np.bool` or `np.bool_`                           | N/A                             | `bool` (defined in `stdbool.h`)                | Boolean (True or False) stored as a byte.                                                     |
| `np.int8`                                            | `np.byte`                    | `signed char`                                  | Platform-defined integer type with 8 bits.                                                    |
| `np.uint8`                                           | `np.ubyte`                   | `unsigned char`                                | Platform-defined integer type with 8 bits without sign.                                       |
| `np.int16`                                           | `np.short`                   | `short`                                        | Platform-defined integer type with 16 bits.                                                   |
| `np.uint16`                                          | `np.ushort`                  | `unsigned short`                               | Platform-defined integer type with 16 bits without sign.                                      |
| `np.int32`                                           | `np.intc`                    | `int`                                          | Platform-defined integer type with 32 bits.                                                   |
| `np.uint32`                                          | `np.uintc`                   | `unsigned int`                                 | Platform-defined integer type with 32 bits without sign.                                      |
| `np.intp`                                            | N/A                             | `ssize_t` / `Py_ssize_t`                       | Platform-defined integer of size `size_t`; used e.g. for sizes.                               |
| `np.uintp`                                           | N/A                             | `size_t`                                       | Platform-defined integer type capable of storing the maximum allocation size.                 |
| N/A                                                     | `'p'`                           | `intptr_t`                                     | Guaranteed to hold pointers. Character code only (Python and C).                              |
| N/A                                                     | `'P'`                           | `uintptr_t`                                    | Guaranteed to hold pointers. Character code only (Python and C).                              |
| `np.int32` or `np.int64`                          | `np.long`                    | `long`                                         | Platform-defined integer type with at least 32 bits.                                          |
| `np.uint32` or `np.uint64`                        | `np.ulong`                   | `unsigned long`                                | Platform-defined integer type with at least 32 bits without sign.                             |
| N/A                                                     | `np.longlong`                | `long long`                                    | Platform-defined integer type with at least 64 bits.                                          |
| N/A                                                     | `np.ulonglong`               | `unsigned long long`                           | Platform-defined integer type with at least 64 bits without sign.                             |
| `np.float16`                                         | `np.half`                    | N/A                                            | Half precision float: sign bit, 5 bits exponent, 10 bits mantissa.                            |
| `np.float32`                                         | `np.single`                  | `float`                                        | Platform-defined single precision float: typically sign bit, 8 bits exponent, 23 bits mantissa.|
| `np.float64`                                         | `np.double`                  | `double`                                       | Platform-defined double precision float: typically sign bit, 11 bits exponent, 52 bits mantissa.|
| `np.float96` or `np.float128`                     | `np.longdouble`              | `long double`                                  | Platform-defined extended-precision float.                                                    |
| `np.complex64`                                       | `np.csingle`                 | `float complex`                                | Complex number, represented by two single-precision floats (real and imaginary components).    |
| `np.complex128`                                      | `np.cdouble`                 | `double complex`                               | Complex number, represented by two double-precision floats (real and imaginary components).    |
| `np.complex192` or `np.complex256`                | `np.clongdouble`             | `long double complex`                          | Complex number, represented by two extended-precision floats (real and imaginary components).  |

In [78]:
x = np.float64(1.0)
print(type(x))
print(type(x) == np.float64)
print(x.dtype == 'float64')

<class 'numpy.float64'>
True
True


#### Machine limits for floating point types

In [92]:
print(np.finfo(np.float16))

Machine parameters for float16
---------------------------------------------------------------
precision =   3   resolution = 1.00040e-03
machep =    -10   eps =        9.76562e-04
negep =     -11   epsneg =     4.88281e-04
minexp =    -14   tiny =       6.10352e-05
maxexp =     16   max =        6.55040e+04
nexp =        5   min =        -max
smallest_normal = 6.10352e-05   smallest_subnormal = 5.96046e-08
---------------------------------------------------------------



In [93]:
print(np.finfo(np.float32))

Machine parameters for float32
---------------------------------------------------------------
precision =   6   resolution = 1.0000000e-06
machep =    -23   eps =        1.1920929e-07
negep =     -24   epsneg =     5.9604645e-08
minexp =   -126   tiny =       1.1754944e-38
maxexp =    128   max =        3.4028235e+38
nexp =        8   min =        -max
smallest_normal = 1.1754944e-38   smallest_subnormal = 1.4012985e-45
---------------------------------------------------------------



In [88]:
print(np.finfo(np.float64))

Machine parameters for float64
---------------------------------------------------------------
precision =  15   resolution = 1.0000000000000001e-15
machep =    -52   eps =        2.2204460492503131e-16
negep =     -53   epsneg =     1.1102230246251565e-16
minexp =  -1022   tiny =       2.2250738585072014e-308
maxexp =   1024   max =        1.7976931348623157e+308
nexp =       11   min =        -max
smallest_normal = 2.2250738585072014e-308   smallest_subnormal = 4.9406564584124654e-324
---------------------------------------------------------------



In [104]:
print(np.finfo(np.longdouble))

Machine parameters for float64
---------------------------------------------------------------
precision =  15   resolution = 1.0000000000000001e-15
machep =    -52   eps =        2.2204460492503131e-16
negep =     -53   epsneg =     1.1102230246251565e-16
minexp =  -1022   tiny =       2.2250738585072014e-308
maxexp =   1024   max =        1.7976931348623157e+308
nexp =       11   min =        -max
smallest_normal = 2.2250738585072014e-308   smallest_subnormal = 4.9406564584124654e-324
---------------------------------------------------------------



In [79]:
print(np.finfo(np.float128))

Machine parameters for float128
---------------------------------------------------------------
precision =  18   resolution = 1.0000000000000000715e-18
machep =    -63   eps =        1.084202172485504434e-19
negep =     -64   epsneg =     5.42101086242752217e-20
minexp = -16382   tiny =       3.3621031431120935063e-4932
maxexp =  16384   max =        1.189731495357231765e+4932
nexp =       15   min =        -max
---------------------------------------------------------------



If there is an error when you run above code: The error AttributeError: module 'numpy' has no attribute 'float128' occurs because the availability of numpy.float128 depends on the platform you’re using. Specifically:

> On most 64-bit Linux systems, numpy.float128 is available and provides extended precision (128-bit floating point).
> On Windows and macOS, numpy.float128 is generally not supported due to limitations in the hardware or compilers used for those systems.

In [80]:
x = np.float64(1.1)
y = np.float64(2.2)
print(x + y)
print(type(x+y))

3.3000000000000003
<class 'numpy.float64'>


In [111]:
x = 1.
print(x + 2 ** -52)

1.0000000000000002


In [112]:
print(2 ** -52)

2.220446049250313e-16


In [82]:
import numpy as np
# x will lose of some digits
x = np.float64(123.456456456456456456456456456456456456)
print(f"Original number: {x:.36g}")

Original number: 123.456456456456450609948660712689161


In [85]:
# 2 ** -53 cannot be saved.
1. + 2 ** -53 == 1

True

In [84]:
1. + 2 ** -52 == 1

False

In [88]:
x = np.float64(1.)
y = np.float64(1. + 2. ** -52)
print(y - x)
x = np.float64(1.)
y = np.float64(1. + 2. ** -53)
print(x + y == 2.)
x = np.float64(0)
y = np.float64(2.11 * 10. ** -310)
print(x + y)

2.220446049250313e-16
True
2.10999999999997e-310


In [93]:
smallest_normalized = np.finfo(np.float64).tiny
print(f"Smallest positive normalized float64: {smallest_normalized:.16e}")
print(smallest_normalized > 0.)

Smallest positive normalized float64: 2.2250738585072014e-308
True


In [92]:

try:
    # Try accessing smallest_subnormal
    finfo = np.finfo(np.float64)
    smallest_subnormal = np.finfo(np.float64).smallest_subnormal
    print(f"Smallest positive subnormal float64: {smallest_subnormal:.16e}")
    print(smallest_subnormal > 0.)
except AttributeError as e:
    # Handle the case when 'smallest_subnormal' is not available
    print("Error:", e)
    # Fallback to manual calculation
    smallest_subnormal = np.float64(2) ** (finfo.minexp - finfo.nmant)
    print("Smallest subnormal calculated manually:", smallest_subnormal)

Error: 'finfo' object has no attribute 'smallest_subnormal'
Smallest subnormal calculated manually: 5e-324


In [94]:
x = 2.9406564584124654e-324 # will around to the smallest number
print(f"{x:.16e}")
x = 1.9406564584124654e-324 # cannt around to the smallest number
print(f"{x:.16e}")
print(1.9406564584124654e-324 > 0.)
print(1.9406564584124654e-324 == 0.)

4.9406564584124654e-324
0.0000000000000000e+00
False
True


In [97]:
import numpy as np
print(np.finfo(np.longdouble))

Machine parameters for float128
---------------------------------------------------------------
precision =  18   resolution = 1.0000000000000000715e-18
machep =    -63   eps =        1.084202172485504434e-19
negep =     -64   epsneg =     5.42101086242752217e-20
minexp = -16382   tiny =       3.3621031431120935063e-4932
maxexp =  16384   max =        1.189731495357231765e+4932
nexp =       15   min =        -max
---------------------------------------------------------------



In [104]:
x = np.float64(1.7976931348623157e+308)
y = np.float64(1.7976931348623157e+308)
print(x,y)

# Suppress RuntimeWarnings
with warnings.catch_warnings():
    warnings.simplefilter("ignore", category=RuntimeWarning)
    # This code that might trigger the warning
    x = np.float64(1e308)
    y = np.float64(1e308)
    print(x + y)  # This would typically trigger the overflow warning

1.7976931348623157e+308 1.7976931348623157e+308
inf


#### Example of non-associativity in floating point arithmetic

In [17]:
# Example of non-associativity in floating point arithmetic
a = 1.0e16
b = -1.0e16
c = 1.0

# Associativity in addition
add_first = (a + b) + c
add_second = a + (b + c)
# Collect results
print(f"a: {a:.17e}")
print(f"b: {b:.17e}")
print(f"c: {c:.17e}")
print(f"b + c: {b + c:.17e}")
print(f"Addition ((a + b) + c): {add_first:.17e}")
print(f"Addition (a + (b + c)): {add_second:.17e}")
print(add_first == add_second)
mul_first = (a * b) * c
mul_second = a * (b * c)

print(f"Multiplication ((a * b) * c): {mul_first:.19e}")
print(f"Multiplication (a * (b * c)): {mul_second:.19e}")
print(mul_first == mul_second)

print('-'*60)

# Associativity in multiplication
a = 0.1
b = 0.2
c = 0.3
add_first = (a + b) + c
add_second = a + (b + c)
# Collect results
print(f"a: {a:.17e}")
print(f"b: {b:.17e}")
print(f"c: {c:.17e}")
print(f"b + c: {b + c:.17e}")
print(f"Addition ((a + b) + c): {add_first:.17e}")
print(f"Addition (a + (b + c)): {add_second:.17e}")
print(add_first == add_second)

mul_first = (a * b) * c
mul_second = a * (b * c)

print(f"Multiplication ((a * b) * c): {mul_first:.19e}")
print(f"Multiplication (a * (b * c)): {mul_second:.19e}")
print(mul_first == mul_second)

a: 1.00000000000000000e+16
b: -1.00000000000000000e+16
c: 1.00000000000000000e+00
b + c: -1.00000000000000000e+16
Addition ((a + b) + c): 1.00000000000000000e+00
Addition (a + (b + c)): 0.00000000000000000e+00
False
Multiplication ((a * b) * c): -1.0000000000000000537e+32
Multiplication (a * (b * c)): -1.0000000000000000537e+32
True
------------------------------------------------------------
a: 1.00000000000000006e-01
b: 2.00000000000000011e-01
c: 2.99999999999999989e-01
b + c: 5.00000000000000000e-01
Addition ((a + b) + c): 6.00000000000000089e-01
Addition (a + (b + c)): 5.99999999999999978e-01
False
Multiplication ((a * b) * c): 6.0000000000000009923e-03
Multiplication (a * (b * c)): 6.0000000000000001249e-03
False


#### Naive sum vs pairwise sum

In [109]:
def naive_sum(x_arr):
    x_sum = np.float64(0.)
    for i in range(len(x_arr)):
        x_sum += x_arr[i]
    return x_sum

def pairwise_sum(x_arr):
    # numpy sum uses pairwise sum algorithm.
    # See details in np.sum API: 
    # https://numpy.org/doc/stable/reference/generated/numpy.sum.html
    return np.sum(x)

# 10M elements of 100000.1
x_arr = np.asarray([100000.1]*10000000, dtype=np.float64)
x_sum_true = 1000001000000.
x_naive_sum = naive_sum(x_arr)
x_pairwise_sum = pairwise_sum(x_arr)

print(f'the accumulated error in naive_sum: {np.abs(x_sum_true - x_naive_sum)}')
print(f'the accumulated error in pairwise_sum: {np.abs(x_sum_true - x_pairwise_sum)}')

the accumulated error in naive_sum: 165.1890869140625
the accumulated error in pairwise_sum: 0.02099609375


#### Be careful when you are using x == y for numerical values

In [114]:
x = .1
print(f"x  : {x: .20e}")
y = .9
print(f"y  : {y: .20e}")
print(f"x+y: {x + y: .20e}")
z = 1.
print(f"z  : {z: .20e}")
print(z == x + y)

x  :  1.00000000000000005551e-01
y  :  9.00000000000000022204e-01
x+y:  1.00000000000000000000e+00
z  :  1.00000000000000000000e+00
True


In [116]:
x = 0.1
print(f"x  : {x: .20e}")
y = 0.2
print(f"y  : {y: .20e}")
print(f"x+y: {x + y: .20e}")
z = 0.3
print(f"z  : {z: .20e}")
print(z == x + y)

x  :  1.00000000000000005551e-01
y  :  2.00000000000000011102e-01
x+y:  3.00000000000000044409e-01
z  :  2.99999999999999988898e-01
False


#### When condition number is large, the error could be large or small.

In [120]:
np.random.seed(1)
x = np.random.normal(loc=0.0, scale=1.0, size=10000000)
print(f'condition number: {np.sum(np.abs(x)) / np.abs(np.sum(x))}')
print(np.sum(x))
x_sum = 0.
for i in range(len(x)):
    x_sum += x[i]
print(x_sum)
print(x_sum - np.sum(x))
x = np.abs(x)
print(f'condition number: {np.sum(np.abs(x)) / np.abs(np.sum(x))}')
print(np.sum(x))
x_sum = 0.
for i in range(len(x)):
    x_sum += x[i]
print(x_sum)
print(x_sum - np.sum(x))

condition number: 9305.973334988492
-857.2282554014972
-857.2282554012562
2.41016095969826e-10
condition number: 1.0
7977343.286765037
7977343.286764891
-1.4621764421463013e-07
